Copyright (c) Microsoft Corporation. All rights reserved.

Licensed under the MIT License.

# Assess Fairness and Mitigate Unfairness
## Overview of Tutorial
This notebook is Part 4 of a four part workshop that demonstrates how to use [InterpretML](interpret.ml) and [Fairlearn](fairlearn.org) (and their integrations with Azure Machine Learning) to understand and analyze models better. The different components of the workshop are as follows:

- Part 1: [Interpretability with glassbox models (EBM)](https://github.com/microsoft/ResponsibleAI-Airlift/blob/main/Interpret/EBM/Interpretable%20Classification%20Methods.ipynb)
- Part 2: [Explain blackbox models with SHAP (and upload explanations to Azure Machine Learning)](https://github.com/microsoft/ResponsibleAI-Airlift/blob/main/Interpret/SHAP/explain-model-SHAP.ipynb)
- Part 3: [Run Interpretability on Azure Machine Learning](https://github.com/microsoft/ResponsibleAI-Airlift/blob/main/Interpret/SHAP/explain-model-Azure.ipynb)
- Part 4: [Model fairness assessment and unfairness mitigation](https://github.com/microsoft/ResponsibleAI-Airlift/blob/main/Fairness/AI-fairness-Census.ipynb) (HERE)

## Introduction

This notebook shows how to use `Fairlearn` and `InterpretML` and their visualizations dashboards to understand a binary classification model. The classification model has been trained on census data, which given a range of data about 32,000 individuals, predicts whether their annual income is above or below fifty thousand dollars per year.

For the purposes of this notebook, we shall treat this as a loan decision problem. We will pretend that the label indicates whether or not each individual repaid a loan in the past. We will use the data to train a predictor to predict whether previously unseen individuals will repay a loan or not. The assumption is that the model predictions are used to decide whether an individual should be offered a loan.

We will first train a fairness-unaware predictor and show that it leads to unfair decisions under a specific notion of fairness called *demographic parity*. We then mitigate unfairness by applying the `GridSearch` algorithm from `Fairlearn` package.

## Install Required Packages

In [27]:
#!pip install --upgrade fairlearn==0.4.6
#%pip uninstall --yes interpret-community
#%pip install --upgrade interpret-community[visualization]
#%pip install --upgrade azureml-interpret
#%pip install --upgrade azureml-contrib-interpret
#!pip install --upgrade azureml-contrib-fairness

#!pip install matplotlib
!pip install azureml-contrib-fairness

After installing packages, you must close and reopen the notebook as well as restarting the kernel.

## Load and preprocess the data set

For simplicity, we import the data set from the `shap` package, which contains the data in a cleaned format. We start by importing the various modules we're going to use:

In [5]:
from fairlearn.reductions import GridSearch
from fairlearn.reductions import DemographicParity, ErrorRate

from sklearn import svm, neighbors, tree
from sklearn.preprocessing import LabelEncoder,StandardScaler
from sklearn.linear_model import LogisticRegression
from sklearn.pipeline import Pipeline
from sklearn.impute import SimpleImputer
from sklearn.preprocessing import StandardScaler, OneHotEncoder
from sklearn.svm import SVC

import pandas as pd
import numpy as np
import shap
shap.initjs()

# SHAP Tabular Explainer
from interpret.ext.blackbox import KernelExplainer

We can now load and inspect the data from the `shap` package:

In [6]:
X_raw, Y = shap.datasets.adult()
X_raw
X_raw["Race"].value_counts().to_dict()

{4: 27816, 2: 3124, 1: 1039, 0: 311, 3: 271}

We are going to treat the sex of each individual as a protected attribute (where 0 indicates female and 1 indicates male), and in this particular case we are going separate this attribute out and drop it from the main data. We then perform some standard data preprocessing steps to convert the data into a format suitable for the ML algorithms

In [7]:
A = X_raw[['Sex','Race']]
#X = pd.get_dummies(X)


le = LabelEncoder()
Y = le.fit_transform(Y)

Finally, we split the data into training and test sets:

In [8]:
from sklearn.model_selection import train_test_split
X_train, X_test, Y_train, Y_test, A_train, A_test = train_test_split(X_raw, 
                                                    Y, 
                                                    A,
                                                    test_size = 0.2,
                                                    random_state=0,
                                                    stratify=Y)

# Work around indexing bug
X_train = X_train.reset_index(drop=True)
A_train = A_train.reset_index(drop=True)
X_test = X_test.reset_index(drop=True)
A_test = A_test.reset_index(drop=True)

# Improve labels
A_test.Sex.loc[(A_test['Sex'] == 0)] = 'female'
A_test.Sex.loc[(A_test['Sex'] == 1)] = 'male'


A_test.Race.loc[(A_test['Race'] == 0)] = 'Amer-Indian-Eskimo'
A_test.Race.loc[(A_test['Race'] == 1)] = 'Asian-Pac-Islander'
A_test.Race.loc[(A_test['Race'] == 2)] = 'Black'
A_test.Race.loc[(A_test['Race'] == 3)] = 'Other'
A_test.Race.loc[(A_test['Race'] == 4)] = 'White'


A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy


## Training a fairness-unaware predictor

To show the effect of `Fairlearn` we will first train a standard ML predictor that does not incorporate fairness For speed of demonstration, we use a simple logistic regression estimator from `sklearn`:

In [9]:
from sklearn.compose import ColumnTransformer

column_tranformer = ColumnTransformer([('onehot', OneHotEncoder(handle_unknown='ignore'), ['Sex', 'Country', 'Race', 'Workclass', 'Marital Status', 'Occupation',
       'Relationship']),
                                       ('scaler', StandardScaler(), ['Capital Gain', 'Capital Loss', 'Hours per week', 'Education-Num'])])


In [10]:
# Append classifier to preprocessing pipeline.
# Now we have a full prediction pipeline.
clf = Pipeline(steps=[('preprocessor', column_tranformer),
                      ('classifier', LogisticRegression(solver='liblinear', fit_intercept=True))])

In [11]:
model = clf.fit(X_train, Y_train)

## Generate Model Explanations

In [12]:
# Using SHAP KernelExplainer
# clf.steps[-1][1] returns the trained classification model
explainer = KernelExplainer(clf.steps[-1][1], 
                             initialization_examples=X_train, 
                             features=X_raw.columns, 
                             classes=['Rejected', 'Approved'], 
                             transformations=column_tranformer)

### Generate global explanations
Explain overall model predictions (global explanation)

In [13]:
global_explanation = explainer.explain_global(X_test)

l1_reg="auto" is deprecated and in the next version (v0.29) the behavior will change from a conditional use of AIC to simply "num_features(10)"!
l1_reg="auto" is deprecated and in the next version (v0.29) the behavior will change from a conditional use of AIC to simply "num_features(10)"!
l1_reg="auto" is deprecated and in the next version (v0.29) the behavior will change from a conditional use of AIC to simply "num_features(10)"!


In [14]:
global_explanation.get_feature_importance_dict()

{'Marital Status': 0.12264592934015234,
 'Education-Num': 0.05829217400491364,
 'Occupation': 0.05295492496502374,
 'Capital Gain': 0.030578697613477607,
 'Relationship': 0.02702108678645073,
 'Sex': 0.021992873466516377,
 'Hours per week': 0.021161345183613563,
 'Capital Loss': 0.010760407843615774,
 'Workclass': 0.009304480059904502,
 'Country': 0.0043782929509755125,
 'Race': 0.0017667852534667416,
 'Age': 0.0}

### Generate local explanations
Explain local data points (individual instances)

In [15]:
# You can pass a specific data point or a group of data points to the explain_local function
# E.g., Explain the first data point in the test set
instance_num = 1
local_explanation = explainer.explain_local(X_test[:instance_num])

l1_reg="auto" is deprecated and in the next version (v0.29) the behavior will change from a conditional use of AIC to simply "num_features(10)"!


In [16]:
# Get the prediction for the first member of the test set and explain why model made that prediction
prediction_value = clf.predict(X_test)[instance_num]

sorted_local_importance_values = local_explanation.get_ranked_local_values()[prediction_value]
sorted_local_importance_names = local_explanation.get_ranked_local_names()[prediction_value]

In [17]:
print('local importance values: {}'.format(sorted_local_importance_values))
print('local importance names: {}'.format(sorted_local_importance_names))

local importance values: [[0.04395646808940118, 0.021755585398355176, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, -0.050016086967474026, -0.18484828742724496]]
local importance names: [['Education-Num', 'Relationship', 'Country', 'Hours per week', 'Capital Loss', 'Capital Gain', 'Sex', 'Race', 'Workclass', 'Age', 'Occupation', 'Marital Status']]


## Visualize model explanations
Load the interpretability visualization dashboard

In [18]:
from interpret_community.widget import ExplanationDashboard

In [19]:
ExplanationDashboard(global_explanation, model, datasetX=X_test, trueY=Y_test)

We can load this predictor into the Fairness dashboard, and examine how it is unfair (there is a warning about AzureML since we are not yet integrated with that product):

## Assess model fairness 
Load the fairness visualization dashboard

In [20]:
from fairlearn.widget import FairlearnDashboard

y_pred = model.predict(X_test)


FairlearnDashboard(sensitive_features=A_test,
                   sensitive_feature_names=['Sex', 'Race'],
                   y_true=Y_test.tolist(),
                   y_pred=[y_pred.tolist()])

FairlearnWidget(value={'true_y': [0, 0, 0, 0, 0, 0, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 1, 0…

Looking at the disparity in accuracy, we see that males have an error rate about three times greater than the females. More interesting is the disparity in opportunitiy - males are offered loans at three times the rate of females.

Despite the fact that we removed the feature from the training data, our predictor still discriminates based on sex. This demonstrates that simply ignoring a protected attribute when fitting a predictor rarely eliminates unfairness. There will generally be enough other features correlated with the removed attribute to lead to disparate impact.

## Mitigation with GridSearch

The `GridSearch` class in `Fairlearn` implements a simplified version of the exponentiated gradient reduction of [Agarwal et al. 2018](https://arxiv.org/abs/1803.02453). The user supplies a standard ML estimator, which is treated as a blackbox. `GridSearch` works by generating a sequence of relabellings and reweightings, and trains a predictor for each.

For this example, we specify demographic parity (on the protected attribute of sex) as the fairness metric. Demographic parity requires that individuals are offered the opportunity (are approved for a loan in this example) independent of membership in the protected class (i.e., females and males should be offered loans at the same rate). We are using this metric for the sake of simplicity; in general, the appropriate fairness metric will not be obvious.

In [21]:
sweep = GridSearch(LogisticRegression(solver='liblinear', fit_intercept=True),
                   constraints=DemographicParity(),
                   grid_size=70)

Our algorithms provide `fit()` and `predict()` methods, so they behave in a similar manner to other ML packages in Python. We do however have to specify two extra arguments to `fit()` - the column of protected attribute labels, and also the number of predictors to generate in our sweep.

After `fit()` completes, we extract the full set of predictors from the `GridSearch` object.

In [23]:
sweep.fit(X_train, Y_train,
          sensitive_features=A_train.Sex)

predictors = sweep._predictors

AssertionError: data can be loaded only once

We could load these predictors into the Fairness dashboard now. However, the plot would be somewhat confusing due to their number. In this case, we are going to remove the predictors which are dominated in the error-disparity space by others from the sweep (note that the disparity will only be calculated for the protected attribute; other potentially protected attributes will not be mitigated). In general, one might not want to do this, since there may be other considerations beyond the strict optimisation of error and disparity (of the given protected attribute).

In [24]:
errors, disparities = [], []
for m in predictors:
    classifier = lambda X: m.predict(X)
    
    error = ErrorRate()
    error.load_data(X_train, pd.Series(Y_train), sensitive_features=A_train.Sex)
    disparity = DemographicParity()
    disparity.load_data(X_train, pd.Series(Y_train), sensitive_features=A_train.Sex)
    
    errors.append(error.gamma(classifier)[0])
    disparities.append(disparity.gamma(classifier).max())
    
all_results = pd.DataFrame( {"predictor": predictors, "error": errors, "disparity": disparities})

all_models_dict = {"census_unmitigated": model}
dominant_models_dict = {"census_unmitigated": model}
base_name_format = "census_grid_model_{0}"
row_id = 0
for row in all_results.itertuples():
    model_name = base_name_format.format(row_id)
    all_models_dict[model_name] = row.predictor
    errors_for_lower_or_eq_disparity = all_results["error"][all_results["disparity"]<=row.disparity]
    if row.error <= errors_for_lower_or_eq_disparity.min():
        dominant_models_dict[model_name] = row.predictor
    row_id = row_id + 1
    

We can construct predictions for all the models, and also for the dominant models:

In [25]:
dashboard_all = dict()
models_all = dict()
for name, predictor in all_models_dict.items():
    value = predictor.predict(X_test)
    dashboard_all[name] = value
    models_all[name] = predictor

In [26]:
FairlearnDashboard(sensitive_features=A_test, 
                   sensitive_feature_names=['Sex', 'Race'],
                   y_true=Y_test.tolist(),
                   y_pred=dashboard_all)


FairlearnWidget(value={'true_y': [0, 0, 0, 0, 0, 0, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 1, 0…

In [ ]:
# Using SHAP KernelExplainer
# clf.steps[-1][1] returns the trained classification model
#winner_model = models_all['census_grid_model_6']
#explainer = KernelExplainer(winner_model, 
#                             initialization_examples=X_train, 
#                             features=X_raw.columns, 
#                             classes=['Rejected', 'Approved'])

In [ ]:
#global_exp=explainer.explain_global(X_test)

In [ ]:
#global_exp.get_feature_importance_dict()

In [ ]:
#ExplanationDashboard(global_exp, winner_model, datasetX=X_train, trueY=Y_test)

We can look at just the dominant models in the dashboard:

We see a Pareto front forming - the set of predictors which represent optimal tradeoffs between accuracy and disparity i predictions. In the ideal case, we would have a predictor at (1,0) - perfectly accurate and without any unfairness under demographic parity (with respect to the protected attribute "sex"). The Pareto front represents the closest we can come to this ideal based on our data and choice of estimator. Note the range of the axes - the disparity axis covers more values than the accuracy, so we can reduce disparity substantially for a small loss in accuracy.

By clicking on individual models on the plot, we can inspect their metrics for disparity and accuracy in greater detail. In a real example, we would then pick the model which represented the best trade-off between accuracy and disparity given the relevant business constraints.

# AzureML Integration

We will now go through a brief example of the AzureML integration.

The required package can be installed via:

```
pip install azureml-contrib-fairness 
```

## Connect To Workspace

Just like in the previous tutorials, we will need to connect to a [workspace](https://docs.microsoft.com/en-us/python/api/azureml-core/azureml.core.workspace(class)?view=azure-ml-py).

The following code will allow you to create a workspace if you don't already have one created. You must have an Azure subscription to create a workspace:

```python
from azureml.core import Workspace
ws = Workspace.create(name='myworkspace',
                      subscription_id='<azure-subscription-id>',
                      resource_group='myresourcegroup',
                      create_resource_group=True,
                      location='eastus2')
```

**If you are running this on a Notebook VM, you can import the existing workspace.**

In [28]:
from azureml.core import Workspace

ws = Workspace.from_config()
print(ws.name, ws.resource_group, ws.location, ws.subscription_id, sep='\n')

If you run your code in unattended mode, i.e., where you can't give a user input, then we recommend to use ServicePrincipalAuthentication or MsiAuthentication.
Please refer to aka.ms/aml-notebook-auth for different authentication mechanisms in azureml-sdk.


devmlws
unilever-mls-dev
westeurope
0d27f570-c739-4d79-b6fd-2f04ad265ab2


## Registering Models

The fairness dashboard is designed to integrate with registered models, so we need to do this for the models we want in the Studio portal. The assumption is that the names of the models specified in the dashboard dictionary correspond to the `id`s (i.e. `<name>:<version>` pairs) of registered models in the workspace.

Next, we register each of the models in the `dashboard_predicted` dictionary into the workspace. For this, we have to save each model to a file, and then register that file:

In [29]:
import joblib
import os
from azureml.core import Model, Experiment, Run

os.makedirs('models', exist_ok=True)
def register_model(name, model):
    print("Registering ", name)
    model_path = "models/{0}.pkl".format(name)
    joblib.dump(value=model, filename=model_path)
    registered_model = Model.register(model_path=model_path,
                                      model_name=name,
                                      workspace=ws)
    print("Registered ", registered_model.id)
    return registered_model.id

model_name_id_mapping = dict()
for name, model in dashboard_all.items():
    m_id = register_model(name, model)
    model_name_id_mapping[name] = m_id

Registering  census_unmitigated
Registering model census_unmitigated
Registered  census_unmitigated:1
Registering  census_grid_model_0
Registering model census_grid_model_0
Registered  census_grid_model_0:1
Registering  census_grid_model_1
Registering model census_grid_model_1
Registered  census_grid_model_1:1
Registering  census_grid_model_2
Registering model census_grid_model_2
Registered  census_grid_model_2:1
Registering  census_grid_model_3
Registering model census_grid_model_3
Registered  census_grid_model_3:1
Registering  census_grid_model_4
Registering model census_grid_model_4
Registered  census_grid_model_4:1
Registering  census_grid_model_5
Registering model census_grid_model_5
Registered  census_grid_model_5:1
Registering  census_grid_model_6
Registering model census_grid_model_6
Registered  census_grid_model_6:1
Registering  census_grid_model_7
Registering model census_grid_model_7
Registered  census_grid_model_7:1
Registering  census_grid_model_8
Registering model census_

Now, produce new predictions dictionaries, with the updated names:

In [30]:
dashboard_all_ids = dict()
for name, y_pred in dashboard_all.items():
    dashboard_all_ids[model_name_id_mapping[name]] = y_pred

## Uploading a dashboard

We create a _dashboard dictionary_ using Fairlearn's `metrics` package. The `_create_group_metric_set` method has arguments similar to the Dashboard constructor, except that the sensitive features are passed as a dictionary (to ensure that names are available), and we must specify the type of prediction. Note that we use the `dashboard_registered` dictionary we just created:

In [32]:
sf = { 'sex': A_test.Sex, 'race': A_test.Race }

from fairlearn.metrics._group_metric_set import _create_group_metric_set


dash_dict_all = _create_group_metric_set(y_true=Y_test,
                                         predictions=dashboard_all_ids,
                                         sensitive_features=sf,
                                         prediction_type='binary_classification')

Precision is ill-defined and being set to 0.0 due to no predicted samples. Use `zero_division` parameter to control this behavior.
Precision is ill-defined and being set to 0.0 due to no predicted samples. Use `zero_division` parameter to control this behavior.
Precision is ill-defined and being set to 0.0 due to no predicted samples. Use `zero_division` parameter to control this behavior.
Precision is ill-defined and being set to 0.0 due to no predicted samples. Use `zero_division` parameter to control this behavior.
Precision is ill-defined and being set to 0.0 due to no predicted samples. Use `zero_division` parameter to control this behavior.
Precision is ill-defined and being set to 0.0 due to no predicted samples. Use `zero_division` parameter to control this behavior.
Precision is ill-defined and being set to 0.0 due to no predicted samples. Use `zero_division` parameter to control this behavior.
Precision is ill-defined and being set to 0.0 due to no predicted samples. Use `zer

Now, we import our `contrib` package which contains the routine to perform the upload:

In [33]:
from azureml.contrib.fairness import upload_dashboard_dictionary, download_dashboard_by_upload_id

Now we can create an Experiment, then a Run, and upload our dashboard to it:

In [34]:
exp = Experiment(ws, "Fairlearn_InterpretML_Census_Demo")
print(exp)

run = exp.start_logging()
try:
    dashboard_title = "Upload MultiAsset from Grid Search with Census Data Notebook"
    upload_id = upload_dashboard_dictionary(run,
                                            dash_dict_all,
                                            dashboard_name=dashboard_title)
    print("\nUploaded to id: {0}\n".format(upload_id))

    downloaded_dict = download_dashboard_by_upload_id(run, upload_id)
    
    
finally:
    run.complete()


Experiment(Name: Fairlearn_InterpretML_Census_Demo,
Workspace: devmlws)


INFO:/Users/mufy/anaconda/envs/amlexp/lib/python3.8/site-packages/azureml/contrib/fairness/_dashboard_validation.py:Starting validation of dashboard dictionary
INFO:/Users/mufy/anaconda/envs/amlexp/lib/python3.8/site-packages/azureml/contrib/fairness/_dashboard_validation.py:Validation of dashboard dictionary successful
INFO:/Users/mufy/anaconda/envs/amlexp/lib/python3.8/site-packages/azureml/contrib/fairness/_azureml_validation.py:Validating model ids exist
INFO:/Users/mufy/anaconda/envs/amlexp/lib/python3.8/site-packages/azureml/contrib/fairness/_azureml_validation.py:Checking census_grid_model_0:1
INFO:/Users/mufy/anaconda/envs/amlexp/lib/python3.8/site-packages/azureml/contrib/fairness/_azureml_validation.py:Checking census_grid_model_10:1
INFO:/Users/mufy/anaconda/envs/amlexp/lib/python3.8/site-packages/azureml/contrib/fairness/_azureml_validation.py:Checking census_grid_model_11:1
INFO:/Users/mufy/anaconda/envs/amlexp/lib/python3.8/site-packages/azureml/contrib/fairness/_azureml_

INFO:/Users/mufy/anaconda/envs/amlexp/lib/python3.8/site-packages/azureml/contrib/fairness/_azureml_validation.py:Checking census_grid_model_58:1
INFO:/Users/mufy/anaconda/envs/amlexp/lib/python3.8/site-packages/azureml/contrib/fairness/_azureml_validation.py:Checking census_grid_model_59:1
INFO:/Users/mufy/anaconda/envs/amlexp/lib/python3.8/site-packages/azureml/contrib/fairness/_azureml_validation.py:Checking census_grid_model_5:1
INFO:/Users/mufy/anaconda/envs/amlexp/lib/python3.8/site-packages/azureml/contrib/fairness/_azureml_validation.py:Checking census_grid_model_60:1
INFO:/Users/mufy/anaconda/envs/amlexp/lib/python3.8/site-packages/azureml/contrib/fairness/_azureml_validation.py:Checking census_grid_model_61:1
INFO:/Users/mufy/anaconda/envs/amlexp/lib/python3.8/site-packages/azureml/contrib/fairness/_azureml_validation.py:Checking census_grid_model_62:1
INFO:/Users/mufy/anaconda/envs/amlexp/lib/python3.8/site-packages/azureml/contrib/fairness/_azureml_validation.py:Checking ce

INFO:/Users/mufy/anaconda/envs/amlexp/lib/python3.8/site-packages/azureml/contrib/fairness/_specific_uploaders.py:Uploaded prediction to prefix azureml.fairness/dashboard.metrics/6e0f1f63-6275-487c-a8ce-78a6918b7e91/y_pred/99453655-e412-4a86-bfc3-91765ff91335.json
INFO:azureml.FairnessArtifactClient:Uploading to azureml.fairness/dashboard.metrics/6e0f1f63-6275-487c-a8ce-78a6918b7e91/y_pred/8bdec19b-bf63-4467-8c7e-b8824afe66ad.json
INFO:/Users/mufy/anaconda/envs/amlexp/lib/python3.8/site-packages/azureml/contrib/fairness/_specific_uploaders.py:Uploaded prediction to prefix azureml.fairness/dashboard.metrics/6e0f1f63-6275-487c-a8ce-78a6918b7e91/y_pred/8bdec19b-bf63-4467-8c7e-b8824afe66ad.json
INFO:azureml.FairnessArtifactClient:Uploading to azureml.fairness/dashboard.metrics/6e0f1f63-6275-487c-a8ce-78a6918b7e91/y_pred/1ceda111-0ec6-45fa-89e7-126831e26d2a.json
INFO:/Users/mufy/anaconda/envs/amlexp/lib/python3.8/site-packages/azureml/contrib/fairness/_specific_uploaders.py:Uploaded predict

INFO:/Users/mufy/anaconda/envs/amlexp/lib/python3.8/site-packages/azureml/contrib/fairness/_specific_uploaders.py:Uploaded prediction to prefix azureml.fairness/dashboard.metrics/6e0f1f63-6275-487c-a8ce-78a6918b7e91/y_pred/f6730e74-4762-4afb-bcb4-f095aab53d84.json
INFO:azureml.FairnessArtifactClient:Uploading to azureml.fairness/dashboard.metrics/6e0f1f63-6275-487c-a8ce-78a6918b7e91/y_pred/880fdfec-3c70-4632-99e7-c039dbabf4d0.json
INFO:/Users/mufy/anaconda/envs/amlexp/lib/python3.8/site-packages/azureml/contrib/fairness/_specific_uploaders.py:Uploaded prediction to prefix azureml.fairness/dashboard.metrics/6e0f1f63-6275-487c-a8ce-78a6918b7e91/y_pred/880fdfec-3c70-4632-99e7-c039dbabf4d0.json
INFO:azureml.FairnessArtifactClient:Uploading to azureml.fairness/dashboard.metrics/6e0f1f63-6275-487c-a8ce-78a6918b7e91/y_pred/61f10d0e-0f3f-4741-a083-95c3fb9d61f4.json
INFO:/Users/mufy/anaconda/envs/amlexp/lib/python3.8/site-packages/azureml/contrib/fairness/_specific_uploaders.py:Uploaded predict

...

INFO:/Users/mufy/anaconda/envs/amlexp/lib/python3.8/site-packages/azureml/contrib/fairness/_fairness_client.py:Populating y_true
INFO:azureml.FairnessArtifactClient:Downloading from azureml.fairness/dashboard.metrics/6e0f1f63-6275-487c-a8ce-78a6918b7e91/y_true/50062612-e002-476f-895d-4b35930cbafa.json
INFO:/Users/mufy/anaconda/envs/amlexp/lib/python3.8/site-packages/azureml/contrib/fairness/_fairness_client.py:Populating y_pred
INFO:azureml.FairnessArtifactClient:Downloading from azureml.fairness/dashboard.metrics/6e0f1f63-6275-487c-a8ce-78a6918b7e91/y_pred/68a18e50-b1ae-49ce-b65e-b781db9c4f01.json
INFO:azureml.FairnessArtifactClient:Downloading from azureml.fairness/dashboard.metrics/6e0f1f63-6275-487c-a8ce-78a6918b7e91/y_pred/ee52979a-f9aa-4351-8671-f69aecaf58fc.json
INFO:azureml.FairnessArtifactClient:Downloading from azureml.fairness/dashboard.metrics/6e0f1f63-6275-487c-a8ce-78a6918b7e91/y_pred/5a349056-2328-4945-b3c9-70af0d60efab.json
INFO:azureml.FairnessArtifactClient:Downloadin

INFO:azureml.FairnessArtifactClient:Downloading from azureml.fairness/dashboard.metrics/6e0f1f63-6275-487c-a8ce-78a6918b7e91/y_pred/127f9561-8f32-4096-b56f-2efc2ab10b2a.json
INFO:azureml.FairnessArtifactClient:Downloading from azureml.fairness/dashboard.metrics/6e0f1f63-6275-487c-a8ce-78a6918b7e91/y_pred/fea092bc-df6d-4a93-8e98-14f13564cf1b.json
INFO:azureml.FairnessArtifactClient:Downloading from azureml.fairness/dashboard.metrics/6e0f1f63-6275-487c-a8ce-78a6918b7e91/y_pred/e09b591e-26a4-4698-b391-f2c886a22f96.json
INFO:azureml.FairnessArtifactClient:Downloading from azureml.fairness/dashboard.metrics/6e0f1f63-6275-487c-a8ce-78a6918b7e91/y_pred/041b6a54-528d-4eed-9803-22a5af340773.json
INFO:azureml.FairnessArtifactClient:Downloading from azureml.fairness/dashboard.metrics/6e0f1f63-6275-487c-a8ce-78a6918b7e91/y_pred/ef52ef4e-5382-40d8-8b72-6a4bec355fd7.json
INFO:azureml.FairnessArtifactClient:Downloading from azureml.fairness/dashboard.metrics/6e0f1f63-6275-487c-a8ce-78a6918b7e91/y_pre

INFO:azureml.FairnessArtifactClient:Downloading from azureml.fairness/dashboard.metrics/6e0f1f63-6275-487c-a8ce-78a6918b7e91/metrics_set/2154bd84-a0d0-4191-bd0a-436132d94444.json
INFO:azureml.FairnessArtifactClient:Downloading from azureml.fairness/dashboard.metrics/6e0f1f63-6275-487c-a8ce-78a6918b7e91/metrics_set/4e6515a2-9773-4c1a-833f-31163cbdb416.json
INFO:azureml.FairnessArtifactClient:Downloading from azureml.fairness/dashboard.metrics/6e0f1f63-6275-487c-a8ce-78a6918b7e91/metrics_set/585d7f6e-650f-4fbe-aaf2-1f6acc608c73.json
INFO:azureml.FairnessArtifactClient:Downloading from azureml.fairness/dashboard.metrics/6e0f1f63-6275-487c-a8ce-78a6918b7e91/metrics_set/973855e0-08a3-4aff-b779-f9cef44ff48b.json
INFO:azureml.FairnessArtifactClient:Downloading from azureml.fairness/dashboard.metrics/6e0f1f63-6275-487c-a8ce-78a6918b7e91/metrics_set/8eb17bd4-9230-443d-85b8-b86f73fe56bc.json
INFO:azureml.FairnessArtifactClient:Downloading from azureml.fairness/dashboard.metrics/6e0f1f63-6275-487

INFO:azureml.FairnessArtifactClient:Downloading from azureml.fairness/dashboard.metrics/6e0f1f63-6275-487c-a8ce-78a6918b7e91/metrics_set/0c8e2ec2-0973-4887-97a0-1331322d9af2.json
INFO:azureml.FairnessArtifactClient:Downloading from azureml.fairness/dashboard.metrics/6e0f1f63-6275-487c-a8ce-78a6918b7e91/metrics_set/d63d3801-8b2f-4899-ab9c-2be56573aa6d.json
INFO:azureml.FairnessArtifactClient:Downloading from azureml.fairness/dashboard.metrics/6e0f1f63-6275-487c-a8ce-78a6918b7e91/metrics_set/aeb19b9b-d862-4d88-a80c-ce33f7c32162.json
INFO:azureml.FairnessArtifactClient:Downloading from azureml.fairness/dashboard.metrics/6e0f1f63-6275-487c-a8ce-78a6918b7e91/metrics_set/71b4be7f-a44f-4c47-a67e-9ee8fbe785bb.json
INFO:azureml.FairnessArtifactClient:Downloading from azureml.fairness/dashboard.metrics/6e0f1f63-6275-487c-a8ce-78a6918b7e91/metrics_set/022ea298-a13b-4b62-b6b2-5b29d69f03b6.json
INFO:azureml.FairnessArtifactClient:Downloading from azureml.fairness/dashboard.metrics/6e0f1f63-6275-487

INFO:azureml.FairnessArtifactClient:Downloading from azureml.fairness/dashboard.metrics/6e0f1f63-6275-487c-a8ce-78a6918b7e91/metrics_set/dedd61af-1337-480f-8f39-2acdca999b74.json
INFO:azureml.FairnessArtifactClient:Downloading from azureml.fairness/dashboard.metrics/6e0f1f63-6275-487c-a8ce-78a6918b7e91/metrics_set/961dfa29-0a0f-4d61-9901-02c7db230db8.json
INFO:azureml.FairnessArtifactClient:Downloading from azureml.fairness/dashboard.metrics/6e0f1f63-6275-487c-a8ce-78a6918b7e91/metrics_set/5e831e50-b8d7-4ecc-b1d9-df435d468327.json
INFO:azureml.FairnessArtifactClient:Downloading from azureml.fairness/dashboard.metrics/6e0f1f63-6275-487c-a8ce-78a6918b7e91/metrics_set/e69af637-4b4f-422c-8d32-2039fbb69a1e.json
INFO:azureml.FairnessArtifactClient:Downloading from azureml.fairness/dashboard.metrics/6e0f1f63-6275-487c-a8ce-78a6918b7e91/metrics_set/4ed38b4e-3c47-4260-b705-ae1df76c485c.json
INFO:azureml.FairnessArtifactClient:Downloading from azureml.fairness/dashboard.metrics/6e0f1f63-6275-487

## Uploading  explanations




In [35]:
from azureml.contrib.interpret.explanation.explanation_client import ExplanationClient

In [36]:
from azureml.contrib.interpret.explanation.explanation_client import ExplanationClient


client = ExplanationClient.from_run(run)
client.upload_model_explanation(global_explanation, comment = "census data global explanation")